## Extracting from commoncrawl

Even though in the particular question given using nytimes api is better, In a lot of cases using something like 
commoncrawl would be the only option.
Reason->
Not all news websites provide api
The requests are limited, example nytimes allowns only 4k requests in a day and 10 in an hour
You want to use data from multiple sources

Hence in this notebook I have downloaded articles from multiple websites, all published on user provided date. After  doing this the pathway to running LDA is same.

In [2]:
#importing the libraries
import hashlib
import json
import logging
import os
import datetime
from dateutil import parser

#please pip install newsplease and replace the files mentioned in next few paragraphs
from newsplease.crawler import commoncrawl_crawler

## AN IMPORTANT POINT

Since each warc file is very large and I am hindered by the time and resources on my disposal.I definitely can not downlaod each warc file published after that particular date.

I saw few warcs and realized that they are scraped on the same date hence I have made modification in the orginal 
commoncrawl_crawler.py located at ~/anaconda3/lib/python3.6/site-packages/newsplease/crawler.

What I am doing now is that since url name of a particular warc tells us at what date it was published. I use this property to download warcs published on the required date unless article is before 2016.


## SOME IMPORTANT CODE AND CONFIGURATION CHANGES

note that by default newsplease keeps a list of already extracted urls and does not process those urls again assuming that the filter has not changed which is absolutely not true in our case. Hence I have made changes to
the required setting my_continue_prcess.

Another thing is that the code for commoncrawl_extracter.py had some errors which did not allow it to wok with date filters. I rectified the errors and uploaded the modified file.

In [3]:
#some unchanged configurations

# download dir for warc files
my_local_download_dir_warc = './cc_download_warc/'
# download dir for articles
my_local_download_dir_article = './cc_download_articles/'
# if date filtering is strict and news-please could not detect the date of an article, the article will be discarded
# number of extraction processes
my_filter_strict_date = True


# if True, the script checks whether a file has been downloaded already and uses that file instead of downloading
# again. Note that there is no check whether the file has been downloaded completely or is valid!
my_reuse_previously_downloaded_files = True
# continue after error
my_continue_after_error = True
# show the progress of downloading the WARC files
my_show_download_progress = True
# log_level
my_log_level = logging.INFO
# json export style
my_json_export_style = 1  # 0 (minimize), 1 (pretty)

# if True, the WARC file will be deleted after all articles have been extracted from it
my_delete_warc_after_extraction = True

In [4]:
#some changed configuration
#note that by default newplease maintains a list of previously extracted warcs and does not extract those warcs
#again assuming that the filter criterion would not have changed but this is absolutely not true in our case
my_continue_process = False

#numebr of extractin processes
my_number_of_extraction_processes = 4

#Note that for the true question I should have only nytimes in this list. This is just showing that we could handle
#cases of multiple newspaper websites with equal ease.
my_filter_valid_hosts = ['nytimes.com','thehindu.com','theguardian.com','bbc.com','wsj.com']

In [5]:
#taking input of the date

In [14]:
date_str = input("Enter the date in mm-dd-yyyy format\n")

Enter the date in mm-dd-yyyy format
09-08-2017


In [15]:
#converting it into a form required to make request yyyymmdd
print(date_str)
date_trimmed=date_str[6:]+date_str[0:2]+date_str[3:5]
print(date_trimmed)

09-08-2017
20170908


In [16]:
#setting the start date to beginning of that date
my_filter_start_date = parser.parse(date_trimmed)

#setting the end to end of the inputted date
my_filter_end_date = parser.parse(date_trimmed+"235959")


In [18]:
print(my_filter_start_date)
print(my_filter_end_date)

2017-09-08 00:00:00
2017-09-08 23:59:59


In [19]:
#!/usr/bin/env python
"""
git clone https://github.com/fhamborg/news-please.git
"""


__author__ = "Felix Hamborg"
__copyright__ = "Copyright 2017"
__credits__ = ["Sebastian Nagel"]


def __setup__():
    """
    Setup
    :return:
    """
    if not os.path.exists(my_local_download_dir_article):
        os.makedirs(my_local_download_dir_article)


def __get_pretty_filepath(path, article):
    """
    Pretty might be an euphemism, but this function tries to avoid too long filenames, while keeping some structure.
    :param path:
    :param name:
    :return:
    """
    short_filename = hashlib.sha256(article.filename.encode()).hexdigest()
    sub_dir = article.source_domain
    final_path = path + sub_dir + '/'
    if not os.path.exists(final_path):
        os.makedirs(final_path)
    return final_path + short_filename + '.json'


def on_valid_article_extracted(article):
    """
    This function will be invoked for each article that was extracted successfully from the archived data and that
    satisfies the filter criteria.
    :param article:
    :return:
    """
    # do whatever you need to do with the article (e.g., save it to disk, store it in ElasticSearch, etc.)
    with open(__get_pretty_filepath(my_local_download_dir_article, article), 'w') as outfile:
        if my_json_export_style == 0:
            json.dump(article.__dict__, outfile, default=str, separators=(',', ':'))
        elif my_json_export_style == 1:
            json.dump(article.__dict__, outfile, default=str, indent=4, sort_keys=True)
        # ...


if __name__ == '__main__':
    __setup__()
    commoncrawl_crawler.crawl_from_commoncrawl(on_valid_article_extracted,
                                               valid_hosts=my_filter_valid_hosts,
                                               start_date=my_filter_start_date,
                                               end_date=my_filter_end_date,
                                               strict_date=my_filter_strict_date,
                                               reuse_previously_downloaded_files=my_reuse_previously_downloaded_files,
                                               local_download_dir_warc=my_local_download_dir_warc,
                                               continue_after_error=my_continue_after_error,
                                               show_download_progress=my_show_download_progress,
                                               number_of_extraction_processes=my_number_of_extraction_processes,
                                               log_level=my_log_level,
                                               delete_warc_after_extraction=True,
                                               continue_process=True)


INFO:newsplease.crawler.commoncrawl_crawler:executing: aws s3 ls --recursive s3://commoncrawl/crawl-data/CC-NEWS/ --no-sign-request > .tmpaws.txt && awk '{ print $4 }' .tmpaws.txt && rm .tmpaws.txt
INFO:newsplease.crawler.commoncrawl_crawler:found 8 files at commoncrawl.org
INFO:newsplease.crawler.commoncrawl_crawler:found 8 relevant files at commoncrawl.org
INFO:newsplease.crawler.commoncrawl_crawler:creating extraction process pool with 4 processes


['crawl-data/CC-NEWS/2017/09/CC-NEWS-20170908041602-00003.warc.gz', 'crawl-data/CC-NEWS/2017/09/CC-NEWS-20170908095908-00004.warc.gz', 'crawl-data/CC-NEWS/2017/09/CC-NEWS-20170908132724-00000.warc.gz', 'crawl-data/CC-NEWS/2017/09/CC-NEWS-20170908132737-00001.warc.gz', 'crawl-data/CC-NEWS/2017/09/CC-NEWS-20170908171528-00002.warc.gz', 'crawl-data/CC-NEWS/2017/09/CC-NEWS-20170908215135-00003.warc.gz', 'crawl-data/CC-NEWS/2017/09/CC-NEWS-20170908215247-00000.warc.gz', 'crawl-data/CC-NEWS/2017/09/CC-NEWS-20170908215251-00001.warc.gz']


INFO:newsplease.crawler.commoncrawl_extractor:downloading https://commoncrawl.s3.amazonaws.com/crawl-data/CC-NEWS/2017/09/CC-NEWS-20170908041602-00003.warc.gz (local: ./cc_download_warc/https%3A%2F%2Fcommoncrawl.s3.amazonaws.com%2Fcrawl-data%2FCC-NEWS%2F2017%2F09%2FCC-NEWS-20170908041602-00003.warc.gz)
INFO:newsplease.crawler.commoncrawl_extractor:downloading https://commoncrawl.s3.amazonaws.com/crawl-data/CC-NEWS/2017/09/CC-NEWS-20170908095908-00004.warc.gz (local: ./cc_download_warc/https%3A%2F%2Fcommoncrawl.s3.amazonaws.com%2Fcrawl-data%2FCC-NEWS%2F2017%2F09%2FCC-NEWS-20170908095908-00004.warc.gz)
INFO:newsplease.crawler.commoncrawl_extractor:downloading https://commoncrawl.s3.amazonaws.com/crawl-data/CC-NEWS/2017/09/CC-NEWS-20170908132724-00000.warc.gz (local: ./cc_download_warc/https%3A%2F%2Fcommoncrawl.s3.amazonaws.com%2Fcrawl-data%2FCC-NEWS%2F2017%2F09%2FCC-NEWS-20170908132724-00000.warc.gz)
INFO:newsplease.crawler.commoncrawl_extractor:downloading https://commoncrawl.s3.amazona

INFO:newsplease.crawler.commoncrawl_extractor:article discard (http://tass.com/sport/964606)
INFO:newsplease.crawler.commoncrawl_extractor:article discard (http://www.reuters.com/article/autos-takata-rosekind-idUSL1N12M1LD20151022)
INFO:newsplease.crawler.commoncrawl_extractor:article discard (http://vov.vn/the-gioi/anh-suc-tan-pha-khung-khiep-cua-dong-dat-81-do-richter-o-mexico-668726.vov)
INFO:newsplease.crawler.commoncrawl_extractor:statistics
INFO:newsplease.crawler.commoncrawl_extractor:pass = 0, discard = 40, total = 40
INFO:newsplease.crawler.commoncrawl_extractor:extraction from current WARC file started 106.94 milliseconds, 940 microseconds ago; 0.002613 s/article
INFO:newsplease.crawler.commoncrawl_extractor:article discard (http://www.football.fr/transferts/articles/mercato-barca-iniesta-a-parle-a-bartomeu-947528/?sitemap)
INFO:newsplease.crawler.commoncrawl_extractor:article discard (http://www.teinteresa.es/ciencia/muertos-sureste-Mexico-fuerte-terremoto_0_1865813511.html)

INFO:newsplease.crawler.commoncrawl_extractor:article discard (http://www.abc.net.au/news/2017-09-08/aboriginal-organisations-launch-alternative-work-for-dole-scheme/8887410)
INFO:newsplease.crawler.commoncrawl_extractor:article discard (http://cbs4indy.com/2017/09/08/hurricane-irma-weakens-to-category-4-as-it-sets-sights-on-florida/)
INFO:newsplease.crawler.commoncrawl_extractor:article discard (https://federalnewsradio.com/government-news/2017/09/police-father-kills-himself-after-sons-accidental-shooting/)
INFO:newsplease.crawler.commoncrawl_extractor:article discard (http://fr.allafrica.com/stories/201709080335.html)
INFO:newsplease.crawler.commoncrawl_extractor:article discard (http://www.breakingnews.ie/world/yves-saint-laurents-partner-pierre-berge-dies-aged-86-805149.html)
INFO:newsplease.crawler.commoncrawl_extractor:article discard (https://www.tvn-2.com/tecnologia/aplicacion-intentar-mitigar-medicamentos-Egipto_0_4843765646.html)
INFO:newsplease.crawler.commoncrawl_extractor:

...

INFO:newsplease.crawler.commoncrawl_extractor:article discard (https://www.dayafterindia.com/2017/09/08/government-directs-airlines-create-no-fly-list-unruly-passengers/)
INFO:newsplease.crawler.commoncrawl_extractor:statistics
INFO:newsplease.crawler.commoncrawl_extractor:article discard (http://www.elkhabarerriadhi.com/2017/09/06/%D8%B1%D8%B3%D9%85%D9%8A%D8%A7-%D9%85%D9%8A%D9%84%D8%A7%D9%86-%D9%8A%D9%81%D9%82%D8%AF-%D8%AC%D9%87%D9%88%D8%AF-%D9%83%D9%88%D9%86%D8%AA%D9%8A-%D8%A3%D9%85%D8%A7%D9%85-%D9%84%D8%A7%D8%AA%D8%B3%D9%8A/)
INFO:newsplease.crawler.commoncrawl_extractor:pass = 24, discard = 12846, total = 12870
INFO:newsplease.crawler.commoncrawl_extractor:article discard (http://www.20minutes.fr/monde/ouragan-irma/2129183-20170908-video-ouragan-irma-bilan-secours-trajectoire-point-situation-caraibes)
INFO:newsplease.crawler.commoncrawl_extractor:statistics
INFO:newsplease.crawler.commoncrawl_extractor:extraction from current WARC file started 1 minute, 50 seconds ago; 0.008571 s/a

INFO:newsplease.crawler.commoncrawl_extractor:article discard (https://uk.sports.yahoo.com/news/zvonareva-last-four-dalian-105856060.html)
INFO:newsplease.crawler.commoncrawl_extractor:article discard (http://www.portsmouth.co.uk/sport/football/pompey/mccrory-out-to-become-pompey-regular-1-8140336)
INFO:newsplease.crawler.commoncrawl_extractor:article discard (https://www.zuonline.ch/buelach/Skyguide-investiert-15-Millionen-Franken-in-bessere-Radarsysteme/story/17131914)
INFO:newsplease.crawler.commoncrawl_extractor:statistics
INFO:newsplease.crawler.commoncrawl_extractor:pass = 24, discard = 12866, total = 12890
INFO:newsplease.crawler.commoncrawl_extractor:article discard (http://www.reuters.com/article/us-taxation-companies-oecd-idUSKCN0S016320151006)
INFO:newsplease.crawler.commoncrawl_extractor:extraction from current WARC file started 1 minute, 50 seconds ago; 0.008563 s/article
INFO:newsplease.crawler.commoncrawl_extractor:article discard (http://news.nanyangpost.com/2017/09/6_4

  File "/home/ubuntu/anaconda3/lib/python3.6/multiprocessing/process.py", line 258, in _bootstrap
    self.run()
  File "/home/ubuntu/anaconda3/lib/python3.6/multiprocessing/pool.py", line 119, in worker
    result = (True, func(*args, **kwds))
  File "/home/ubuntu/anaconda3/lib/python3.6/multiprocessing/process.py", line 93, in run
    self._target(*self._args, **self._kwargs)
  File "/home/ubuntu/anaconda3/lib/python3.6/multiprocessing/pool.py", line 44, in mapstar
    return list(map(*args))
  File "/home/ubuntu/anaconda3/lib/python3.6/multiprocessing/process.py", line 93, in run
    self._target(*self._args, **self._kwargs)
  File "/home/ubuntu/anaconda3/lib/python3.6/multiprocessing/pool.py", line 119, in worker
    result = (True, func(*args, **kwds))
  File "/home/ubuntu/anaconda3/lib/python3.6/site-packages/newsplease/crawler/commoncrawl_crawler.py", line 146, in __start_commoncrawl_extractor
    log_pathname_fully_extracted_warcs=__log_pathname_fully_extracted_warcs)
  File "/

  File "zmq/backend/cython/context.pyx", line 136, in zmq.backend.cython.context.Context.term
  File "zmq/backend/cython/checkrc.pxd", line 12, in zmq.backend.cython.checkrc._check_rc
  File "/home/ubuntu/anaconda3/lib/python3.6/site-packages/newsplease/crawler/commoncrawl_extractor.py", line 259, in __process_warc_gz_file
    record.rec_headers.get_header('WARC-Target-URI'))
KeyboardInterrupt


KeyboardInterrupt: 

In [20]:
#stopped the process midway. we just need to make sure that we can extract relevant articles

In [21]:
!ls

cc_download_articles  downlaoding_articles_from_commoncrawl.ipynb
cc_download_warc      fullyextractedwarcs.list


In [22]:
ls cc_download_articles/

www.bbc.com/  www.nytimes.com/  www.theguardian.com/  www.wsj.com/


In [26]:
!ls cc_download_articles/www.nytimes.com/

053eb8e3c8558e76fda2d66017f6be684620c33fc46bd60069e689ffecdfd9f9.json
05ef20ea97c3d757fc865154fd4deb1d7b0ca87727ffb4fc74c72f450c4260dd.json
0fd5731ffc0a6d747125db7394694faa080954cf8d9a1b9b9443931e451b0178.json
136ee2b5cf20096a3a579201bcef93dc4a221d3ba6b866d99d826725d9f0568b.json
2553360275e86ea05ce395c9256ac51240436fbe6cbac6333df834c183e2d8a5.json
6e3d12f2077c85eec9edbd04d29d5e0098963b20e2a3144d9692c4b9bf23b560.json
b59d5a8f304d6b4d93c8b474e3d4332f8494aef74a0510ea7b8574273178e001.json
dd066a313b34e67e316bdb4517350984265586884202454418fbf5c3e840fa43.json


In [27]:
folder_name = "/home/ubuntu/unfound_assignment/cc_download_articles/www.theguardian.com/"

In [28]:
filenames = os.listdir(folder_name)

In [38]:
#having a look at one of the articles
articles_in_dic_format = []
try:
    for filename in filenames:
        with open(folder_name+filename,'r') as file:
            articles_in_dic_format.append(json.load(file))
except:
    print("this file might have been corrupted during interupting the program")

In [39]:
len(articles_in_dic_format)

78

In [40]:
sample_article = articles_in_dic_format[0]

In [41]:
sample_article.keys()

dict_keys(['authors', 'date_download', 'date_modify', 'date_publish', 'description', 'filename', 'image_url', 'language', 'localpath', 'source_domain', 'text', 'title', 'title_page', 'title_rss', 'url'])

In [42]:
sample_article['text'][:100]

'Cricket, south London and immigration have a long and fertile shared history. Albeit, in recent year'

In [43]:
#doing the same step as done in nytimes api
simplified_articles = [(str(article['description']) + str(article['text']) + str(article['title']) ) for article in articles_in_dic_format]

In [55]:
#writing to disk

import pickle

with open("the_guardian_cc","wb") as file:
    pickle.dump(simplified_articles,file)


In [57]:
#checking if laod is correct

with open("the_guardian_cc","rb") as infile:
    loaded_articles = pickle.load(infile)

In [58]:
print(simplified_articles==loaded_articles)

True


## GO TO LDA NOTEBOOK